# <span style="color:red">**PinpointAI | Part II**</span>

## CSV Import form Data Collection

In [3]:
import os
import requests
from streetview_api import API_KEY
from PIL import Image
import torch
from torchvision import transforms, models
from torch.utils.data import DataLoader, Dataset, TensorDataset
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import torch.nn as nn
import torch.optim as optim
import pandas as pd

In [4]:
# Define the path to your CSV files
csv_file_path = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/valid_coordinates_fr1.csv'  
csv_file_path = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/valid_coordinates_fr2.csv'  
csv_file_path = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/valid_coordinates_fr3.csv'  
csv_file_path = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/valid_coordinates_fr4.csv'  
csv_file_path = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/valid_coordinates_fr5.csv'  
csv_file_path = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/valid_coordinates_fr6.csv'  
csv_file_path = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/valid_coordinates_fr7.csv'  


# Load the CSV file into a pandas DataFrame
df_coordinates_1 = pd.read_csv(csv_file_path)
df_coordinates_2 = pd.read_csv(csv_file_path)
df_coordinates_3 = pd.read_csv(csv_file_path)
df_coordinates_4 = pd.read_csv(csv_file_path)
df_coordinates_5 = pd.read_csv(csv_file_path)
df_coordinates_6 = pd.read_csv(csv_file_path)
df_coordinates_7 = pd.read_csv(csv_file_path)

## Concat Data frames

In [6]:
# Concatenate the DataFrames
df_combined = pd.concat([df_coordinates_1, df_coordinates_2, df_coordinates_3, df_coordinates_4, df_coordinates_5, df_coordinates_6, df_coordinates_7], ignore_index=True)

In [7]:
# Optionally, save the combined DataFrame to a new CSV
df_combined.to_csv('/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/combined_coordinates.csv', index=False)

## Streetview Images Collection

## Data set duplicate cleaning

In [10]:
# Define the path to your CSV file
csv_file_path = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/combined_coordinates.csv'  # Replace with your actual file path

# Load the CSV file into a pandas DataFrame
combined_coordinates = pd.read_csv(csv_file_path)

In [11]:
# Check for duplicates in the entire dataframe
duplicates = combined_coordinates.duplicated()

# Display duplicates
print(duplicates)

# Count the number of duplicates
num_duplicates = duplicates.sum()
print(f"Number of duplicates in the first 5 rows: {num_duplicates}")


0        False
1        False
2        False
3        False
4        False
         ...  
48925     True
48926     True
48927     True
48928     True
48929     True
Length: 48930, dtype: bool
Number of duplicates in the first 5 rows: 41940


## Image Integrity Check 

In [13]:
# Path to your dataset
dataset_path = "/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image"

# Supported image extensions
valid_extensions = (".jpg", ".jpeg", ".png")

# Check for corrupted images
for filename in os.listdir(dataset_path):
    if filename.lower().endswith(valid_extensions):  # Check if the file is an image
        try:
            img = Image.open(os.path.join(dataset_path, filename))
            img.verify()  # Verify image integrity
        except (IOError, SyntaxError) as e:
            print(f"Corrupted image: {filename}")
    else:
        print(f"Skipping non-image file: {filename}")


Skipping non-image file: .DS_Store
Skipping non-image file: .ipynb_checkpoints


## Split Data
- Divide your dataset into training, validation, and test sets (e.g., 70% training, 20% validation, 10% test).
- Ensure the split is random but balanced across regions or coordinate ranges.

## Custom Dataset Class

In [16]:
class ImageDataset(Dataset):
    def __init__(self, image_paths, transform=None):
        self.image_paths = image_paths
        self.transform = transform

    def __len__(self):
        return len(self.image_paths)

    def __getitem__(self, idx):
        # Ensure image_paths[idx] is a valid path
        image_path = self.image_paths[idx]

        # Open the image
        image = Image.open(image_path).convert("RGB")  # Ensure it's in RGB format

        # Apply transformations if provided
        if self.transform:
            image = self.transform(image)

        return image


## Data Augmentation and Transformation for Training and Validation

In [18]:
# Define transformations
train_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.RandomHorizontalFlip(),  # Augmentation for training
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

val_test_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])


## Loading Dataset using ImageFolder

In [20]:
from torchvision import datasets
from torch.utils.data import DataLoader

# Define your dataset (replace with your own data path)
train_dataset = datasets.ImageFolder(root='/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image', transform=train_transform)
val_dataset = datasets.ImageFolder(root='/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image', transform=val_test_transform)
test_dataset = datasets.ImageFolder(root='/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image', transform=val_test_transform)

# Define DataLoader for batching
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True, num_workers=4)
val_loader = DataLoader(val_dataset, batch_size=32, shuffle=False, num_workers=4)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False, num_workers=4)


## DataLoader Setup

In [22]:
from torch.utils.data import DataLoader

batch_size = 64  # Adjust based on your GPU/CPU memory

train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)


## Model Definition with Pre-trained ResNet18

In [24]:
import torch
import torch.nn as nn
from torchvision.models import resnet18, ResNet18_Weights

# Load pre-trained ResNet18 with updated weights parameter
weights = ResNet18_Weights.IMAGENET1K_V1  # Equivalent to the old 'pretrained=True'
model = resnet18(weights=weights)

# Replace the final fully connected layer for regression (output 2 values for latitude and longitude)
model.fc = nn.Linear(model.fc.in_features, 2)  # 2 outputs for lat/lon

# Now the model is ready for regression (latitude and longitude prediction)


## Model Training Loop | Regression Model

In [26]:
image_directory = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image'
image_filenames = [f for f in os.listdir(image_directory) if f.endswith(('.jpeg', '.jpg'))]
print(f"Total images found: {len(image_filenames)}")


Total images found: 25172


In [27]:
coordinates_file = 'image_coordinates.csv'  # Replace with the correct CSV file path
coordinates_df = pd.read_csv(coordinates_file)
print(f"Total coordinates found: {len(coordinates_df)}")


Total coordinates found: 25172


In [28]:
# Path to the images folder
images_folder = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image'
coordinates_file = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/combined_coordinates.csv'

# Read the coordinates file (assuming it has a list of latitudes and longitudes)
with open(coordinates_file, 'r') as f:
    coordinates = [line.strip().split(',') for line in f.readlines()]

# List all image filenames in the images folder
image_filenames = os.listdir(images_folder)

# Create a list of tuples (image_filename, latitude, longitude)
data = []
coordinate_index = 0
for image_filename in image_filenames:
    if image_filename.endswith('.jpg') or image_filename.endswith('.jpeg'):
        # Check if there is a corresponding coordinate
        if coordinate_index < len(coordinates):
            lat, lon = coordinates[coordinate_index]  # Get the corresponding latitude and longitude
            data.append([image_filename, lat, lon])
            coordinate_index += 1

# Convert to a DataFrame and save to CSV
df = pd.DataFrame(data, columns=['image', 'latitude', 'longitude'])
df.to_csv('image_coordinates.csv', index=False)

print("CSV file created: image_coordinates.csv")


CSV file created: image_coordinates.csv


In [29]:
# Verify consistency between CSV and image folder
csv_file = 'image_coordinates.csv'
images_folder = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image'

coordinates_frame = pd.read_csv(csv_file)
all_images = set(os.listdir(images_folder))

# Check for missing files
missing_images = coordinates_frame[~coordinates_frame['image'].isin(all_images)]
print(f"Missing images: {len(missing_images)}")
print(missing_images)

# Drop rows with missing images
coordinates_frame = coordinates_frame[coordinates_frame['image'].isin(all_images)]
print(f"Valid rows after removing missing images: {len(coordinates_frame)}")

# Save the cleaned CSV
coordinates_frame.to_csv('cleaned_image_coordinates.csv', index=False)


Missing images: 0
Empty DataFrame
Columns: [image, latitude, longitude]
Index: []
Valid rows after removing missing images: 25172


## Freezing Pre-trained Layers

In [31]:
# Define the model class
class StreetViewModel(nn.Module):
    def __init__(self):
        super(StreetViewModel, self).__init__()
        weights = models.ResNet18_Weights.IMAGENET1K_V1
        self.resnet = models.resnet18(weights=weights)
        self.resnet.fc = nn.Linear(self.resnet.fc.in_features, 2)  # 2 outputs for lat/lon

    def forward(self, x):
        return self.resnet(x)

# Instantiate the model
model = StreetViewModel()

# Step 1: Freeze earlier layers and fine-tune the FC layer
for param in model.parameters():
    param.requires_grad = False  # Freeze earlier layers

# Unfreeze the classifier layer (self.resnet.fc)
for param in model.resnet.fc.parameters():
    param.requires_grad = True  # Unfreeze the classifier layer

# Use Adam optimizer for the fine-tuned FC layer
optimizer = torch.optim.Adam(model.resnet.fc.parameters(), lr=1e-4)  # Start with a higher LR for FC

# Step 2: Gradually unfreeze layers after initial training
# Example: Unfreeze the last ResNet block (self.resnet.layer4)
for param in model.resnet.layer4.parameters():
    param.requires_grad = True

# Update optimizer to include both the FC layer and the unfreezed layer4
optimizer = torch.optim.Adam([
    {'params': model.resnet.fc.parameters(), 'lr': 1e-4},  # Higher LR for FC
    {'params': model.resnet.layer4.parameters(), 'lr': 1e-5}  # Lower LR for layer4
])

# Print model summary (optional)
print(model)


StreetViewModel(
  (resnet): ResNet(
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): BasicBlock(
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (relu): ReLU(inplace=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      )
      (1): BasicBlock(
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, tr

## Training Loop with Gradients

In [33]:
class ImageCoordinates:
    def __init__(self, file_path):
        self.coordinates_frame = pd.read_csv(file_path, header=0)

# Example usage
data = ImageCoordinates('cleaned_image_coordinates.csv')
print(data.coordinates_frame.head())


                   image            latitude           longitude
0  streetview_19241.jpeg            Latitude           Longitude
1  streetview_10963.jpeg   45.97443188715016  -1.334913216821063
2   streetview_3170.jpeg    47.3426554357292   5.981062096215023
3  streetview_11671.jpeg  48.480374537243975   7.005046081223238
4  streetview_14189.jpeg  43.680951823881315  2.7856177851274007


In [ ]:
import os
import pandas as pd
from PIL import Image
import torch
from torch.utils.data import Dataset, DataLoader
import torch.nn as nn
import torch.optim as optim
from torchvision import models, transforms

# Ensure the dataset class is defined
class StreetViewDataset(Dataset):
    def __init__(self, csv_file, root_dir, transform=None):
        # Load and clean the CSV file
        self.coordinates_frame = pd.read_csv(csv_file, header=0)
        
        # Drop invalid rows where latitude or longitude are not numeric
        self.coordinates_frame = self.coordinates_frame[
            pd.to_numeric(self.coordinates_frame['latitude'], errors='coerce').notna()
        ]
        self.coordinates_frame = self.coordinates_frame[
            pd.to_numeric(self.coordinates_frame['longitude'], errors='coerce').notna()
        ]
        self.coordinates_frame.reset_index(drop=True, inplace=True)
        
        self.root_dir = root_dir
        self.transform = transform

    def __len__(self):
        return len(self.coordinates_frame)

    def __getitem__(self, idx):
        img_name = os.path.join(self.root_dir, self.coordinates_frame.iloc[idx, 0])
        
        # Check if the image file exists
        if not os.path.exists(img_name):
            print(f"File not found: {img_name}")
            return None, None  # Handle missing file gracefully
        
        print(f"Loading image: {img_name}")  # Debugging line
        image = Image.open(img_name).convert("RGB")
        
        latitude = float(self.coordinates_frame.iloc[idx, 1])
        longitude = float(self.coordinates_frame.iloc[idx, 2])
        label = [latitude, longitude]

        if self.transform:
            image = self.transform(image)

        return image, torch.tensor(label, dtype=torch.float32)


# Define the model class
class StreetViewModel(nn.Module):
    def __init__(self):
        super(StreetViewModel, self).__init__()
        weights = models.ResNet18_Weights.IMAGENET1K_V1
        self.resnet = models.resnet18(weights=weights)
        self.resnet.fc = nn.Linear(self.resnet.fc.in_features, 2)  # 2 outputs for lat/lon

    def forward(self, x):
        return self.resnet(x)

# Set the device to CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Instantiate the model
model = StreetViewModel()
model.to(device)

# Define the loss function and optimizer
criterion = nn.MSELoss()  # For regression tasks
optimizer = optim.Adam([
    {'params': model.resnet.fc.parameters(), 'lr': 1e-4},  # Higher LR for FC
    {'params': model.resnet.layer4.parameters(), 'lr': 1e-5}  # Lower LR for layer4
])

# Dataset and DataLoader setup
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Replace with your actual CSV and image directory
csv_file = 'cleaned_image_coordinates.csv'  # Ensure this file is cleaned
images_folder = '/Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image'

# Custom dataset and dataloader
train_dataset = StreetViewDataset(csv_file=csv_file, root_dir=images_folder, transform=transform)
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True, num_workers=0)  # Set num_workers=0 for debugging

# Paths for saving model and losses
model_save_path = "streetview_model.pth"
loss_save_path = "training_losses.csv"

# Load the model and optimizer state if available
if os.path.exists(model_save_path):
    checkpoint = torch.load(model_save_path)
    model.load_state_dict(checkpoint['model_state_dict'])
    optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
    start_epoch = checkpoint['epoch'] + 1
    print(f"Resuming training from epoch {start_epoch}")
else:
    start_epoch = 0

# Training loop
num_epochs = 10  # Adjust the number of epochs as needed
all_losses = []

for epoch in range(start_epoch, num_epochs):
    model.train()  # Set the model to training mode
    train_loss = 0.0

    for batch in train_loader:
        images, labels = batch  # Unpack images and labels
        if images is None:  # Skip batches where image loading failed
            continue
        images = images.to(device)
        labels = labels.to(device).float()  # Ensure labels are float

        # Zero the gradients
        optimizer.zero_grad()

        # Forward pass
        outputs = model(images)

        # Compute the loss
        loss = criterion(outputs, labels)  # MSELoss for regression
        train_loss += loss.item()

        # Backward pass and optimization
        loss.backward()  # Compute gradients
        optimizer.step()  # Update the weights

    epoch_loss = train_loss / len(train_loader)
    all_losses.append(epoch_loss)
    print(f"Epoch {epoch+1}/{num_epochs}, Loss: {epoch_loss:.4f}")

    # Save the model after every epoch
    torch.save({
        'epoch': epoch,
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': optimizer.state_dict()
    }, model_save_path)

# Save losses to a CSV file
loss_df = pd.DataFrame(all_losses, columns=["Loss"])
loss_df.to_csv(loss_save_path, index=False)
print("Training complete. Model and losses saved.")


/var/folders/t2/40gs14tj4lg2536r26vzcyv40000gn/T/ipykernel_9900/811639914.py:98: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(model_save_path)


Resuming training from epoch 1
Loading image: /Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image/streetview_8362.jpeg
Loading image: /Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image/streetview_5609.jpeg
Loading image: /Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image/streetview_10800.jpeg
Loading image: /Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image/streetview_16526.jpeg
Loading image: /Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image/streetview_7177.jpeg
Loading image: /Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image/streetview_6273.jpeg
Loading image: /Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image/streetview_23458.jpeg
Loading image: /Users/mbouch17/Desktop/Personal_Data_Project/PinpointAI/jpeg_streetview_image/streetview_6149.jpeg
Loading image: /Users/mbouch17/Desktop/Persona

## Validation Loop

In [ ]:
# Set the model to evaluation mode and disable gradient calculation
with torch.no_grad():
    model.eval()  # Set the model to evaluation mode
    val_loss = 0.0
    
    # Iterate over the validation dataset
    for images, labels in val_loader:
        images, labels = images.to(device), labels.to(device)
        
        # Forward pass
        outputs = model(images)
        
        # Compute the loss
        loss = criterion(outputs, labels)
        
        # Accumulate the loss
        val_loss += loss.item()

    # Average the validation loss over all batches
    print(f"Validation Loss: {val_loss / len(val_loader):.4f}")


In [ ]:
print('lol')

## Test the Model

In [ ]:
test_loss = 0.0
correct = 0
total = 0

with torch.no_grad():
    model.eval()
    for images, labels in test_loader:
        images, labels = images.to(device), labels.to(device)
        outputs = model(images)

        # Compute loss
        loss = criterion(outputs, labels)
        test_loss += loss.item()

        # Compute accuracy
        _, predicted = torch.max(outputs, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

print(f"Test Loss: {test_loss / len(test_loader):.4f}")
print(f"Test Accuracy: {100 * correct / total:.2f}%")


In [ ]:
import matplotlib.pyplot as plt
import numpy as np

# Function to denormalize the image
def denormalize_image(tensor, mean, std):
    mean = torch.tensor(mean).view(1, 3, 1, 1)
    std = torch.tensor(std).view(1, 3, 1, 1)
    tensor = tensor * std + mean  # Reverse the normalization
    return tensor

model.eval()
with torch.no_grad():
    for images, labels in test_loader:
        images, labels = images.to(device), labels.to(device)
        outputs = model(images)
        _, predicted = torch.max(outputs, 1)

        # Denormalize the image for visualization
        denormalized_image = denormalize_image(images[0], mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
        denormalized_image = denormalized_image.squeeze().cpu().numpy().transpose(1, 2, 0)  # Convert to HWC format

        # Clip values to be in range [0, 1]
        denormalized_image = np.clip(denormalized_image, 0, 1)

        # Display the image
        plt.imshow(denormalized_image)
        plt.title(f"True: {labels[0].item()}, Predicted: {predicted[0].item()}")
        plt.show()
        break  # Display just one image


## Save & Deploy Model

In [ ]:
#Save the model
torch.save(model.state_dict(), "fine_tuned_model.pth")


In [ ]:
model.load_state_dict(torch.load("fine_tuned_model.pth", weights_only=True))
